# Q Table Learning

Example of reinforcement learning using Q-Learning with table method, and the ["FrozenLake"](https://gym.openai.com/envs/FrozenLake-v0) environment of [OpenAI gym](https://gym.openai.com/)

## Frozen Lake environment and problem description
In this example, the AI agent is located in a 4X4 grid, the surface of every cell in the grid can be described with one of the following:
* S: starting point(safe)
* F: frozen surface(safe)
* H: hole(unsafe surface, the agent falls the problem is finished unsuccesfully)
* G: goal(safe surface, this is where the agent needs to go ,if the agent gets here its rewarded)

The objective of the agent is to learn a way to reach the G(goal) state ,if it reaches the goal state gets a reward,else gets no reward. The 4X4 grid is defined as the following(creating 16 possible states):

SFFF

FHFH

FFFH

HFFG

For example:

State 0 is the agent being in initial state(starting point S).

From state 0 if the agent moves right, will reach state 1(F frozen surface)

From state 0 if the agent moves down, will reach state 4(F frozen surface)

From state 4, if the agent moves right, will reach state 5(H hole, it will fall and end the episode with no reward)



## Frozen lake solution with Q-Table learning

In [1]:
import gym
import numpy as np
from gym.envs.registration import register

### Import Frozen lake environment from OpenAI gym
In the original frozen lake environment theres a "slippery" property that makes the state reached as the result of an action in a given state non-deterministic, to make the example simpler, the is_slippery flag is removed,so the reached state as result of an action a, in a state s, is always the same 

In [2]:
register(
    id='FrozenLakeNotSlippery-v0',
    entry_point='gym.envs.toy_text:FrozenLakeEnv',
    kwargs={'map_name' : '4x4', 'is_slippery': False},
    max_episode_steps=100,
    reward_threshold=0.78, # optimum = .8196
)

In [3]:
frozenLakeEnv =  gym.make('FrozenLakeNotSlippery-v0')

[2017-08-14 00:48:42,139] Making new env: FrozenLakeNotSlippery-v0


In [4]:
actions_dictionary = {0:"left",1:"down",2:"right",3:"up"}

### Q-table learning reinforcement learning algorithm

In [5]:
# Initialize learning parameters
learning_rate = 0.8
discount_factor = 0.95 #the importance of future rewards,0 means only current reward matters(ignore future rewards)
num_episodes = 50000 #number of  iterations (from initial state, to final state)
max_steps_per_episode = 100 #maximum number allowed to execute per episode
initial_explore_probability = 0.50 #the agent will explore with e probability, and exploit best action(from q table) with 1-e probability

In [6]:
# Initialize q table with zeros ,dimensions: statesXactions
Qtable = np.zeros([frozenLakeEnv.observation_space.n,frozenLakeEnv.action_space.n])
# Counts the number of times an action is taken in a given state
taken_action_count = np.zeros([frozenLakeEnv.observation_space.n,frozenLakeEnv.action_space.n])

# Create a list to contain steps per episode, and rewards per episode
steps_per_episode = []
rewards_per_episode = []

for episode in range(num_episodes):
    #print("#### Starting episode "+str(episode))
    # Reset environment and get first state
    state = frozenLakeEnv.reset()
    episode_rewards = 0
    episode_steps = 0
    state_is_final = False
    step_behavior = "" #will indicate if agent is exploring or exploiting
    episode_state_sequence = str(state) #sequence of states the agent will be in every episode
    explore_probability = initial_explore_probability*(1-episode/num_episodes)
    #print(explore_probability)
    
    for step in range(max_steps_per_episode):
        #frozenLakeEnv.render()
        # Chose an action exploring with e probability and exploiting(best action from q table) with 1-e prob.
        if np.random.rand(1) < explore_probability:
            # explore
            action = frozenLakeEnv.action_space.sample()
            step_behavior = "R"
        else:
            # exploit best action(selected from Q table)
            action = np.argmax(Qtable[state,:])
            step_behavior = "B"
            
        # Given current state, and selected action, get new state , action reward and "is final" flag
        new_state,reward,state_is_final,_ = frozenLakeEnv.step(action)
        episode_rewards+=reward
        # if its not succesfull final state,create punishment
        reward = -1 if state_is_final and reward == 0 else reward
        # Update Qtable for current state and selected action using bellman equation
        Qtable[state,action] += learning_rate*(reward+discount_factor*np.max(Qtable[new_state,:])-Qtable[state,action])
            
        # Update the episode step count 
        episode_steps+=1
        
        #Set that the new step's state is the new state reached by selected action
        state=new_state
        episode_state_sequence = episode_state_sequence+"->"+step_behavior+str(state)
        
        # If the state is final(goal state or failure state, exit)
        if state_is_final:
            break
            
    steps_per_episode.append(episode_steps)
    rewards_per_episode.append(episode_rewards)
    
    if state_is_final and reward > 0:
        print("Reached goal state in episode "+str(episode)+ " after "+ str(step) +" steps,average score in time: "+str(sum(rewards_per_episode)/num_episodes)+ ",stage sequence:"+ episode_state_sequence)

Reached goal state in episode 1295 after 8 steps,average score in time: 2e-05,stage sequence:0->R1->B0->R4->B8->R8->R9->R13->R14->R15
Reached goal state in episode 1387 after 14 steps,average score in time: 4e-05,stage sequence:0->B0->B0->B0->B0->B0->R0->R4->R8->B8->B8->B8->R9->R13->R14->B15
Reached goal state in episode 1389 after 7 steps,average score in time: 6e-05,stage sequence:0->R4->B8->B8->R9->R13->R13->B14->B15
Reached goal state in episode 1390 after 18 steps,average score in time: 8e-05,stage sequence:0->B0->R4->B8->B8->B8->B8->B8->B8->R4->B8->B8->R8->R4->B8->B8->R9->B13->R14->B15
Reached goal state in episode 1393 after 9 steps,average score in time: 0.0001,stage sequence:0->B4->B8->B9->R10->B9->B13->B14->R13->B14->B15
Reached goal state in episode 1394 after 5 steps,average score in time: 0.00012,stage sequence:0->R4->B8->B9->R13->B14->B15
Reached goal state in episode 1396 after 7 steps,average score in time: 0.00014,stage sequence:0->R0->R0->B4->B8->B9->R13->B14->R15
Rea

Reached goal state in episode 2052 after 10 steps,average score in time: 0.00546,stage sequence:0->R0->B4->R0->B4->R0->R1->B2->R6->B10->B14->B15
Reached goal state in episode 2055 after 6 steps,average score in time: 0.00548,stage sequence:0->R0->B4->B8->R9->R10->B14->B15
Reached goal state in episode 2057 after 7 steps,average score in time: 0.0055,stage sequence:0->R0->R1->B2->B6->B10->B14->R14->B15
Reached goal state in episode 2058 after 7 steps,average score in time: 0.00552,stage sequence:0->B4->B8->B9->R10->B14->R13->R14->R15
Reached goal state in episode 2062 after 6 steps,average score in time: 0.00554,stage sequence:0->R0->R1->B2->B6->B10->B14->B15
Reached goal state in episode 2064 after 9 steps,average score in time: 0.00556,stage sequence:0->R0->B4->B8->B9->R8->R8->B9->R10->R14->B15
Reached goal state in episode 2065 after 5 steps,average score in time: 0.00558,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 2070 after 7 steps,average score in tim

Reached goal state in episode 2853 after 10 steps,average score in time: 0.01218,stage sequence:0->B4->B8->R4->R0->B4->R4->B8->R9->R13->R14->B15
Reached goal state in episode 2858 after 6 steps,average score in time: 0.0122,stage sequence:0->R0->B4->R8->R9->B13->B14->B15
Reached goal state in episode 2859 after 7 steps,average score in time: 0.01222,stage sequence:0->B4->B8->R9->B13->R9->B13->B14->R15
Reached goal state in episode 2864 after 7 steps,average score in time: 0.01224,stage sequence:0->B4->R4->R4->B8->B9->B13->B14->B15
Reached goal state in episode 2865 after 10 steps,average score in time: 0.01226,stage sequence:0->R0->R4->R0->R4->B8->B9->B13->R14->R14->R14->B15
Reached goal state in episode 2866 after 17 steps,average score in time: 0.01228,stage sequence:0->B4->B8->B9->R8->B9->B13->B14->R10->B14->R10->R9->R8->R9->B13->R9->R13->R14->B15
Reached goal state in episode 2867 after 5 steps,average score in time: 0.0123,stage sequence:0->B4->B8->B9->B13->R14->B15
Reached goal s

Reached goal state in episode 3604 after 5 steps,average score in time: 0.01934,stage sequence:0->B4->B8->B9->B13->R14->B15
Reached goal state in episode 3615 after 5 steps,average score in time: 0.01936,stage sequence:0->R1->B2->B6->B10->B14->B15
Reached goal state in episode 3616 after 8 steps,average score in time: 0.01938,stage sequence:0->R0->B4->B8->B9->B13->B14->R13->B14->B15
Reached goal state in episode 3618 after 5 steps,average score in time: 0.0194,stage sequence:0->B4->B8->B9->R13->B14->B15
Reached goal state in episode 3620 after 5 steps,average score in time: 0.01942,stage sequence:0->B4->R8->R9->R10->B14->B15
Reached goal state in episode 3623 after 6 steps,average score in time: 0.01944,stage sequence:0->B4->B8->B9->B13->B14->R14->B15
Reached goal state in episode 3624 after 7 steps,average score in time: 0.01946,stage sequence:0->R1->B2->R3->B2->B6->B10->R14->B15
Reached goal state in episode 3625 after 5 steps,average score in time: 0.01948,stage sequence:0->B4->B8->

Reached goal state in episode 4280 after 13 steps,average score in time: 0.02538,stage sequence:0->R4->B8->R8->R8->B9->R8->B9->R10->B14->R10->B14->R10->B14->B15
Reached goal state in episode 4285 after 6 steps,average score in time: 0.0254,stage sequence:0->B4->R4->R8->R9->B13->R14->R15
Reached goal state in episode 4286 after 6 steps,average score in time: 0.02542,stage sequence:0->B4->R8->B9->B13->R13->R14->B15
Reached goal state in episode 4288 after 6 steps,average score in time: 0.02544,stage sequence:0->R4->R4->R8->B9->B13->B14->B15
Reached goal state in episode 4289 after 5 steps,average score in time: 0.02546,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 4290 after 5 steps,average score in time: 0.02548,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 4295 after 7 steps,average score in time: 0.0255,stage sequence:0->R1->B2->B6->B10->B14->R10->B14->B15
Reached goal state in episode 4301 after 5 steps,average score in time: 0.

...

Reached goal state in episode 48144 after 5 steps,average score in time: 0.67258,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48145 after 5 steps,average score in time: 0.6726,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48146 after 5 steps,average score in time: 0.67262,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48147 after 5 steps,average score in time: 0.67264,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48148 after 5 steps,average score in time: 0.67266,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48149 after 5 steps,average score in time: 0.67268,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48150 after 5 steps,average score in time: 0.6727,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48151 after 5 steps,average score in time: 0.67272,stage sequence:0->B4->B8->B9->B13->B14->B15
Re

Reached goal state in episode 48604 after 5 steps,average score in time: 0.68162,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48605 after 5 steps,average score in time: 0.68164,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48606 after 5 steps,average score in time: 0.68166,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48607 after 5 steps,average score in time: 0.68168,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48609 after 5 steps,average score in time: 0.6817,stage sequence:0->B4->B8->R9->B13->B14->B15
Reached goal state in episode 48610 after 5 steps,average score in time: 0.68172,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48611 after 5 steps,average score in time: 0.68174,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 48612 after 5 steps,average score in time: 0.68176,stage sequence:0->B4->B8->B9->B13->B14->B15
R

Reached goal state in episode 49063 after 5 steps,average score in time: 0.69068,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49064 after 5 steps,average score in time: 0.6907,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49065 after 5 steps,average score in time: 0.69072,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49066 after 5 steps,average score in time: 0.69074,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49067 after 5 steps,average score in time: 0.69076,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49068 after 5 steps,average score in time: 0.69078,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49069 after 5 steps,average score in time: 0.6908,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49070 after 5 steps,average score in time: 0.69082,stage sequence:0->B4->B8->B9->B13->B14->B15
Re

Reached goal state in episode 49520 after 5 steps,average score in time: 0.69974,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49521 after 5 steps,average score in time: 0.69976,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49522 after 5 steps,average score in time: 0.69978,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49523 after 5 steps,average score in time: 0.6998,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49524 after 5 steps,average score in time: 0.69982,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49525 after 5 steps,average score in time: 0.69984,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49526 after 5 steps,average score in time: 0.69986,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49527 after 5 steps,average score in time: 0.69988,stage sequence:0->B4->B8->B9->B13->B14->B15
R

Reached goal state in episode 49970 after 5 steps,average score in time: 0.70874,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49971 after 5 steps,average score in time: 0.70876,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49972 after 5 steps,average score in time: 0.70878,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49973 after 5 steps,average score in time: 0.7088,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49974 after 5 steps,average score in time: 0.70882,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49975 after 5 steps,average score in time: 0.70884,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49976 after 5 steps,average score in time: 0.70886,stage sequence:0->B4->B8->B9->B13->B14->B15
Reached goal state in episode 49977 after 5 steps,average score in time: 0.70888,stage sequence:0->B4->B8->B9->B13->B14->B15
R

In [7]:
print( "Total over time: " +  str(sum(rewards_per_episode)/num_episodes))

Total over time: 0.70932


### Learned Q-table
Interpretation : every row of the Q-table is an state, and every column an action, the values of the table means how good is to take action a in state s, so bigger values mean actions that provide better results(a way to reach the Goal state)

In [8]:
np.set_printoptions(precision=6)
np.set_printoptions(suppress=True)
Qtable

array([[ 0.735092,  0.773781,  0.773781,  0.735092],
       [ 0.735092, -1.      ,  0.814506,  0.773781],
       [ 0.773781,  0.857375,  0.773781,  0.814506],
       [ 0.814506, -1.      ,  0.773781,  0.773781],
       [ 0.773781,  0.814506, -1.      ,  0.735092],
       [ 0.      ,  0.      ,  0.      ,  0.      ],
       [-1.      ,  0.9025  , -1.      ,  0.814506],
       [ 0.      ,  0.      ,  0.      ,  0.      ],
       [ 0.814506, -1.      ,  0.857375,  0.773781],
       [ 0.814506,  0.9025  ,  0.9025  , -1.      ],
       [ 0.857375,  0.95    , -1.      ,  0.857375],
       [ 0.      ,  0.      ,  0.      ,  0.      ],
       [ 0.      ,  0.      ,  0.      ,  0.      ],
       [-1.      ,  0.9025  ,  0.95    ,  0.857375],
       [ 0.9025  ,  0.95    ,  1.      ,  0.9025  ],
       [ 0.      ,  0.      ,  0.      ,  0.      ]])

### Lets see if the agent learned to reach goal state during training:
Set the agent in the initial state and see its route  to goal state

In [9]:
state = frozenLakeEnv.reset()
state_sequence = str(state)
action_sequence = ""
max_steps = 100
is_final_state = False

step_count = 0
while not is_final_state and  step_count < max_steps:
    frozenLakeEnv.render()
    best_action = np.argmax(Qtable[state,:])
    state,_,is_final_state,_ = frozenLakeEnv.step(best_action)
    state_sequence=state_sequence+"->"+str(state)
    action_sequence = action_sequence+"->"+actions_dictionary[best_action]
    step_count += 1
frozenLakeEnv.render()
print("State sequence:"+state_sequence)
print("Action sequence:"+action_sequence)


SFFF
FHFH
FFFH
HFFG
  (Down)
SFFF
FHFH
FFFH
HFFG
  (Down)
SFFF
FHFH
FFFH
HFFG
  (Right)
SFFF
FHFH
FFFH
HFFG
  (Down)
SFFF
FHFH
FFFH
HFFG
  (Right)
SFFF
FHFH
FFFH
HFFG
  (Right)
SFFF
FHFH
FFFH
HFFG
State sequence:0->4->8->9->13->14->15
Action sequence:->down->down->right->down->right->right


### The agent learned to find a way to goal state.
Table method works for small problems but if there are many states and/or many actions its not possible to use a table,  a Neural network can  be used that approximates a Q table